In [1]:
import torch
import torchvision
import torchvision.transforms as transforms
import time

In [3]:
st = time.time()
# defining the transfor which is only making it a tensor 
transform = transforms.ToTensor()

batch_size = 10 #how many units in each insert in the pipeline

#  declaring the training set as the train.csv file from the stated directory
trainset = torchvision.datasets.FER2013(root='./biai-proj/data', split="train",
                                         transform=transform) 

# setting up the loader (aka iterator) for the train set 
trainloader = torch.utils.data.DataLoader(trainset, batch_size=batch_size,
                                          shuffle=True, num_workers=0)

# repeating for the test set
testset = torchvision.datasets.FER2013(root='./biai-proj/data', split="test",
                                        transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=batch_size,
                                         shuffle=False, num_workers=0)

classes = ("Angry", "Disgust", "Fear", "Happy", "Sad", "Surprise", "Neutral")

In [5]:
print(type(trainset))

<class 'torchvision.datasets.fer2013.FER2013'>


In [4]:
print(trainset)

Dataset FER2013
    Number of datapoints: 28709
    Root location: ./biai-proj/data
    split=train
    StandardTransform
Transform: ToTensor()


In [19]:

# this part is only to test if I can get images from the set 

import matplotlib.pyplot as plt
import numpy as np

# functions to show an image
def imshow(img):
#     commented since we did not normalize in the first place
#     img = img / 2 + 0.5     # unnormalize
    npimg = img.numpy()
    plt.imshow(np.transpose(npimg, (1, 2, 0)))
    plt.show()


# get some random training images
dataiter = iter(testloader)
images, labels = next(dataiter)

# show images
imshow(torchvision.utils.make_grid(images))
# print labels
print(' '.join(f'{classes[labels[j]]:5s}' for j in range(batch_size)))

TypeError: default_collate: batch must contain tensors, numpy arrays, numbers, dicts or lists; found <class 'NoneType'>

In [6]:
# Check that MPS is available
if not torch.backends.mps.is_available():
    if not torch.backends.mps.is_built():
        print("MPS not available because the current PyTorch install was not "
              "built with MPS enabled.")
    else:
        print("MPS not available because the current MacOS version is not 12.3+ "
              "and/or you do not have an MPS-enabled device on this machine.")

else:
    print("MPS found")
    mps_device = torch.device("mps")

MPS found


In [13]:
# Design and define the NN 

import torch.nn as nn
import torch.nn.functional as F


class Net(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = nn.Conv2d(1, 6, 5) 
    # output size = 6 *44*44 values 
    # image size : n*n 
    # filter size: f*f (f is odd number)
    # shrinked_image size : (n - f + 1)^2 

        self.pool = nn.MaxPool2d(2, 2) 
    # default stride is 2 because it was not specified so defaults to kernel size which is 2
    # output size = ((n-f+1)/2)^2 = 22*22 *6  
        
        self.conv2 = nn.Conv2d(6, 16, 5)
     #output size = 18 * 18 * 16 = 5184   
        
        self.fc1 = nn.Linear(16 * 9 * 9, 120)
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, 7)

    def forward(self, x):
        x = self.pool(F.relu(self.conv1(x))) 
        # 44*44*6 , 22*22*6 
        
        x = self.pool(F.relu(self.conv2(x)))
        # 18*18*16 , 9*9*16 
        
        x = torch.flatten(x, 1) # flatten all dimensions except batch
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x


net = Net()
# net.to(mps_device)
print(net)

Net(
  (conv1): Conv2d(1, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=1296, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=7, bias=True)
)


In [14]:
import torch.optim as optim

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.001, momentum=0.9)

In [16]:
for epoch in range(2):  # loop over the dataset multiple times

    running_loss = 0.0
    for i, data in enumerate(trainloader, 0):
        # get the inputs; data is a list of [inputs, labels]
        inputs, labels = data
#         inputs, labels = data[0].to(mps_device), data[1].to(mps_device)

        # zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = net(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        # print statistics
        running_loss += loss.item()
        if i % 2000 == 1999:    # print every 2000 mini-batches
            print(f'[{epoch + 1}, {i + 1:5d}] loss: {running_loss / 2000:.3f}')
            running_loss = 0.0
elapsed_time = time.time() - st
print('Execution time:', time.strftime("%H:%M:%S", time.gmtime(elapsed_time)))
print('Finished Training')


[1,  2000] loss: 1.826
[2,  2000] loss: 1.770
Execution time: 00:05:04
Finished Training


In [11]:
PATH = './biai-proj/fer2013_net_testing.pth'
# torch.save(net.state_dict(), PATH)

In [18]:
dataiter = iter(testloader)
images, labels = next(dataiter)

# print images
imshow(torchvision.utils.make_grid(images))
print('GroundTruth: ', ' '.join(f'{classes[labels[j]]:5s}' for j in range(4)))

TypeError: default_collate: batch must contain tensors, numpy arrays, numbers, dicts or lists; found <class 'NoneType'>

In [14]:
net = Net()
# net.load_state_dict(torch.load(PATH))

In [15]:
outputs = net(images)

In [16]:
_, predicted = torch.max(outputs, 1)

print('Predicted: ', ' '.join(f'{classes[predicted[j]]:5s}'
                              for j in range(4)))

Predicted:  Happy Happy Happy Happy


In [22]:
with torch.no_grad():
    for data in trainset:
        print(type(data), data)

<class 'tuple'> (tensor([[[0.2745, 0.3137, 0.3216,  ..., 0.2039, 0.1686, 0.1608],
         [0.2549, 0.2392, 0.2275,  ..., 0.2196, 0.2039, 0.1725],
         [0.1961, 0.1686, 0.2118,  ..., 0.1922, 0.2196, 0.1843],
         ...,
         [0.3569, 0.2549, 0.1647,  ..., 0.2824, 0.2196, 0.1686],
         [0.3020, 0.3216, 0.3098,  ..., 0.4118, 0.2745, 0.1804],
         [0.3020, 0.2824, 0.3294,  ..., 0.4157, 0.4275, 0.3216]]]), 0)
<class 'tuple'> (tensor([[[0.5922, 0.5882, 0.5765,  ..., 0.5059, 0.5490, 0.4706],
         [0.5922, 0.5843, 0.5843,  ..., 0.4784, 0.5529, 0.5373],
         [0.5922, 0.5922, 0.6118,  ..., 0.4275, 0.4824, 0.5725],
         ...,
         [0.7373, 0.7373, 0.4745,  ..., 0.7255, 0.7255, 0.7294],
         [0.7373, 0.7333, 0.7686,  ..., 0.7294, 0.7137, 0.7333],
         [0.7294, 0.7216, 0.7255,  ..., 0.7569, 0.7176, 0.7216]]]), 0)
<class 'tuple'> (tensor([[[0.9059, 0.8314, 0.6118,  ..., 0.1725, 0.1059, 0.0627],
         [0.8980, 0.6863, 0.5804,  ..., 0.1059, 0.1373, 0.1059],

<class 'tuple'> (tensor([[[0.0235, 0.0235, 0.1216,  ..., 0.2314, 0.2118, 0.3804],
         [0.0627, 0.0706, 0.1373,  ..., 0.2980, 0.2235, 0.3922],
         [0.1020, 0.1804, 0.2392,  ..., 0.3961, 0.2863, 0.4039],
         ...,
         [0.1333, 0.1020, 0.1020,  ..., 0.3216, 0.4510, 0.3333],
         [0.0863, 0.0824, 0.1255,  ..., 0.2784, 0.4314, 0.3882],
         [0.1333, 0.1569, 0.2157,  ..., 0.2863, 0.4235, 0.5216]]]), 2)
<class 'tuple'> (tensor([[[0.6471, 0.6549, 0.6706,  ..., 0.9608, 0.9765, 0.9804],
         [0.6588, 0.6667, 0.6706,  ..., 0.8902, 0.9294, 0.9686],
         [0.6745, 0.6784, 0.6588,  ..., 0.8314, 0.8863, 0.9373],
         ...,
         [0.5647, 0.5686, 0.5725,  ..., 0.7569, 0.7647, 0.8157],
         [0.5529, 0.5647, 0.5647,  ..., 0.7529, 0.7882, 0.7608],
         [0.5255, 0.5647, 0.5569,  ..., 0.7647, 0.8039, 0.2863]]]), 2)
<class 'tuple'> (tensor([[[0.4627, 0.4157, 0.4118,  ..., 0.9725, 0.9882, 0.9882],
         [0.4745, 0.4431, 0.4745,  ..., 0.9725, 0.9882, 0.9882],

<class 'tuple'> (tensor([[[0.0549, 0.0549, 0.0706,  ..., 0.7647, 0.7529, 0.8196],
         [0.0627, 0.0627, 0.0588,  ..., 0.6510, 0.6392, 0.6392],
         [0.0588, 0.0588, 0.0510,  ..., 0.3922, 0.3882, 0.4314],
         ...,
         [1.0000, 1.0000, 1.0000,  ..., 0.0588, 0.0588, 0.0588],
         [1.0000, 1.0000, 1.0000,  ..., 0.0549, 0.0549, 0.0627],
         [1.0000, 1.0000, 0.9961,  ..., 0.0510, 0.0510, 0.0510]]]), 2)
<class 'tuple'> (tensor([[[1.0000, 0.9922, 0.9922,  ..., 1.0000, 1.0000, 1.0000],
         [0.9961, 0.9961, 0.9843,  ..., 1.0000, 1.0000, 1.0000],
         [0.9922, 0.9922, 0.7843,  ..., 1.0000, 1.0000, 1.0000],
         ...,
         [0.1961, 0.1725, 0.2431,  ..., 0.4118, 0.2980, 0.2588],
         [0.1569, 0.1176, 0.2510,  ..., 0.4784, 0.2941, 0.2510],
         [0.1216, 0.1059, 0.2118,  ..., 0.4863, 0.2902, 0.2784]]]), 3)
<class 'tuple'> (tensor([[[0.6078, 0.4078, 0.4314,  ..., 0.4824, 0.4627, 0.3961],
         [0.5882, 0.4039, 0.4471,  ..., 0.4980, 0.4588, 0.3882],

<class 'tuple'> (tensor([[[0.4353, 0.3098, 0.0549,  ..., 0.0431, 0.2039, 0.4078],
         [0.4275, 0.2353, 0.0471,  ..., 0.0549, 0.1373, 0.3608],
         [0.4157, 0.1725, 0.0471,  ..., 0.0549, 0.0745, 0.2902],
         ...,
         [0.4039, 0.4039, 0.4039,  ..., 0.3882, 0.3922, 0.3843],
         [0.4039, 0.4078, 0.4078,  ..., 0.3843, 0.3882, 0.3882],
         [0.4078, 0.4118, 0.4078,  ..., 0.3843, 0.3843, 0.3843]]]), 6)
<class 'tuple'> (tensor([[[0.0039, 0.0078, 0.0039,  ..., 1.0000, 1.0000, 1.0000],
         [0.0039, 0.0039, 0.0078,  ..., 1.0000, 1.0000, 1.0000],
         [0.0157, 0.0078, 0.0078,  ..., 1.0000, 1.0000, 1.0000],
         ...,
         [1.0000, 0.9961, 1.0000,  ..., 1.0000, 1.0000, 1.0000],
         [1.0000, 1.0000, 1.0000,  ..., 1.0000, 1.0000, 1.0000],
         [1.0000, 1.0000, 0.9961,  ..., 1.0000, 1.0000, 1.0000]]]), 2)
<class 'tuple'> (tensor([[[0.6118, 0.6353, 0.4353,  ..., 0.5020, 0.4980, 0.4941],
         [0.6275, 0.5961, 0.3098,  ..., 0.5020, 0.5020, 0.4980],

<class 'tuple'> (tensor([[[0.1255, 0.1333, 0.2000,  ..., 0.1373, 0.2039, 0.2941],
         [0.1412, 0.1647, 0.1804,  ..., 0.1020, 0.1098, 0.1333],
         [0.1333, 0.1686, 0.1647,  ..., 0.1176, 0.1020, 0.1020],
         ...,
         [0.0667, 0.0706, 0.0706,  ..., 0.1725, 0.1961, 0.2627],
         [0.0824, 0.0706, 0.0706,  ..., 0.1608, 0.1765, 0.2275],
         [0.0824, 0.0667, 0.0706,  ..., 0.1373, 0.1686, 0.2157]]]), 3)
<class 'tuple'> (tensor([[[0.6863, 0.7255, 0.7529,  ..., 0.6863, 0.6510, 0.6431],
         [0.6980, 0.7333, 0.7608,  ..., 0.7059, 0.6510, 0.6392],
         [0.6863, 0.7137, 0.7294,  ..., 0.7529, 0.7020, 0.6196],
         ...,
         [0.5804, 0.5882, 0.5569,  ..., 0.5373, 0.5451, 0.5490],
         [0.5804, 0.5922, 0.5765,  ..., 0.4980, 0.5529, 0.5529],
         [0.5647, 0.5647, 0.5804,  ..., 0.4980, 0.5529, 0.5451]]]), 6)
<class 'tuple'> (tensor([[[0.1059, 0.1176, 0.1294,  ..., 0.6471, 0.6471, 0.6471],
         [0.1255, 0.1255, 0.1451,  ..., 0.6588, 0.6588, 0.6549],

...

<class 'tuple'> (tensor([[[0.2471, 0.2706, 0.2275,  ..., 0.2941, 0.4039, 0.3843],
         [0.2392, 0.2431, 0.2000,  ..., 0.2588, 0.3765, 0.4431],
         [0.2549, 0.2157, 0.1961,  ..., 0.2353, 0.3373, 0.4392],
         ...,
         [0.7725, 0.8078, 0.8157,  ..., 0.7843, 0.8078, 0.7922],
         [0.7412, 0.8157, 0.8157,  ..., 0.7882, 0.8118, 0.7843],
         [0.7020, 0.8196, 0.8157,  ..., 0.7843, 0.8235, 0.7922]]]), 5)
<class 'tuple'> (tensor([[[0.1137, 0.1098, 0.1137,  ..., 0.2078, 0.3569, 0.2667],
         [0.1137, 0.1059, 0.1137,  ..., 0.2824, 0.3294, 0.2824],
         [0.1059, 0.1059, 0.1059,  ..., 0.3490, 0.3765, 0.2627],
         ...,
         [0.0863, 0.0863, 0.0863,  ..., 0.1765, 0.1686, 0.1608],
         [0.0941, 0.0902, 0.0863,  ..., 0.1765, 0.1725, 0.1686],
         [0.0863, 0.0941, 0.0902,  ..., 0.1922, 0.1804, 0.1725]]]), 4)
<class 'tuple'> (tensor([[[0.6784, 0.7059, 0.5059,  ..., 0.7882, 0.7725, 0.7725],
         [0.6941, 0.6745, 0.3020,  ..., 0.7843, 0.7686, 0.7765],

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



(tensor([[[0.9216, 0.9569, 0.7020,  ..., 0.2980, 0.2471, 0.1961],
         [0.9255, 0.9451, 0.4941,  ..., 0.3137, 0.2588, 0.2118],
         [0.9451, 0.8392, 0.3059,  ..., 0.3176, 0.2784, 0.2392],
         ...,
         [0.7529, 0.4000, 0.3647,  ..., 0.4471, 0.1529, 0.0941],
         [0.7647, 0.4118, 0.3686,  ..., 0.1843, 0.0980, 0.1137],
         [0.7725, 0.4196, 0.3804,  ..., 0.0784, 0.1176, 0.1059]]]), 6)
<class 'tuple'> (tensor([[[0.2235, 0.1961, 0.1843,  ..., 0.1961, 0.6000, 0.8706],
         [0.2157, 0.1882, 0.1373,  ..., 0.3137, 0.6039, 0.8980],
         [0.2275, 0.1843, 0.1765,  ..., 0.3647, 0.6431, 0.9686],
         ...,
         [0.9373, 0.9529, 0.6039,  ..., 0.9412, 0.9333, 0.9294],
         [0.8627, 0.4667, 0.2392,  ..., 0.9294, 0.9255, 0.9333],
         [0.3412, 0.2549, 0.3020,  ..., 0.9294, 0.9216, 0.9294]]]), 6)
<class 'tuple'> (tensor([[[0.6353, 0.6235, 0.6235,  ..., 0.6745, 0.6745, 0.6706],
         [0.6196, 0.6000, 0.5843,  ..., 0.6784, 0.6745, 0.6706],
         [0.592

<class 'tuple'> (tensor([[[0.9725, 0.9725, 0.9725,  ..., 0.1490, 0.1373, 0.1373],
         [0.9765, 0.9725, 0.9725,  ..., 0.1647, 0.1608, 0.1216],
         [0.9765, 0.9765, 0.9765,  ..., 0.1569, 0.1725, 0.1412],
         ...,
         [0.9882, 0.9922, 0.9882,  ..., 0.5333, 0.5569, 0.5490],
         [0.9882, 0.9922, 0.9882,  ..., 0.5490, 0.5569, 0.5373],
         [0.9922, 0.9882, 0.9882,  ..., 0.5569, 0.5529, 0.5373]]]), 3)
<class 'tuple'> (tensor([[[0.8000, 0.7412, 0.7020,  ..., 0.4706, 0.4431, 0.3922],
         [0.7922, 0.7529, 0.7333,  ..., 0.4706, 0.4627, 0.4157],
         [0.7765, 0.7725, 0.7294,  ..., 0.4784, 0.4667, 0.4353],
         ...,
         [0.7255, 0.6980, 0.6471,  ..., 0.3137, 0.3412, 0.3490],
         [0.7216, 0.7059, 0.6078,  ..., 0.5255, 0.4667, 0.5255],
         [0.7294, 0.6667, 0.6235,  ..., 0.7020, 0.7020, 0.7608]]]), 3)
<class 'tuple'> (tensor([[[0.8706, 0.8706, 0.8627,  ..., 0.5725, 0.5843, 0.6118],
         [0.8667, 0.8510, 0.8510,  ..., 0.5333, 0.5529, 0.5647],

<class 'tuple'> (tensor([[[0.2667, 0.2196, 0.2667,  ..., 0.4549, 0.4235, 0.4157],
         [0.2549, 0.1922, 0.2196,  ..., 0.4392, 0.4392, 0.4314],
         [0.2235, 0.1451, 0.2431,  ..., 0.4627, 0.4039, 0.4275],
         ...,
         [0.4510, 0.4471, 0.4706,  ..., 0.6902, 0.8314, 0.7569],
         [0.4431, 0.5020, 0.5176,  ..., 0.6275, 0.8824, 0.8824],
         [0.4706, 0.5412, 0.5333,  ..., 0.6353, 0.8863, 0.9490]]]), 6)
<class 'tuple'> (tensor([[[0.9176, 0.9137, 0.9137,  ..., 0.1294, 0.1216, 0.1255],
         [0.9176, 0.9176, 0.9137,  ..., 0.1098, 0.1137, 0.1137],
         [0.9216, 0.9176, 0.9137,  ..., 0.1020, 0.1098, 0.1176],
         ...,
         [0.9020, 0.8627, 0.8314,  ..., 0.0157, 0.0196, 0.0157],
         [0.8588, 0.8431, 0.8039,  ..., 0.0157, 0.0235, 0.0235],
         [0.8588, 0.8235, 0.8000,  ..., 0.0157, 0.0235, 0.0235]]]), 3)
<class 'tuple'> (tensor([[[0.2510, 0.3020, 0.2157,  ..., 0.4314, 0.4471, 0.5059],
         [0.2118, 0.4353, 0.3725,  ..., 0.4314, 0.4314, 0.5294],

In [18]:
correct = 0
total = 0
# since we're not training, we don't need to calculate the gradients for our outputs
with torch.no_grad():
    for data in testloader:
        images, labels = data
        # calculate outputs by running images through the network
        outputs = net(images)
        # the class with the highest energy is what we choose as prediction
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

print(f'Accuracy of the network on the 10000 test images: {100 * correct // total} %')

TypeError: default_collate: batch must contain tensors, numpy arrays, numbers, dicts or lists; found <class 'NoneType'>